<a href="https://colab.research.google.com/github/alechain/transcrippcion/blob/main/transcribe.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Instalamos las librerias necesarias

In [ ]:

# Para instalas descomentar
#!pip install git+https://github.com/openai/whisper.git -q
#!pip install openai
#!pip install pytube

# Importamos las librerias necesarias

In [5]:
import whisper
import numpy  as np
import pandas as pd
import openai
import os
import sys
import subprocess
import requests
import regex as re
from pytube import YouTube



## Creamos unas función para descargar videos de youtube ( se puede cargar el video mp4 directo en el enviroment) y lo guardamos con el nombre de video.mp4

In [7]:
url='https://www.youtube.com/watch?v=KU3ARgSNhvo'
yt = YouTube(url)
stream_url = yt.streams.filter(progressive=True, file_extension='mp4').order_by('resolution').desc().first().url
response = requests.get(stream_url)
with open("video.mp4", "wb") as f:
    f.write(response.content)

### Ahora lo que viene aca es una funcioncita que basicamente convierte en fomato mp3 el audio del video que le pases (en formato mp4), para eso se usa la función ffmpeg que es una librería para gestion de videos 

In [8]:
def video2mp3(video_file, output_ext="mp3"):
    filename, ext = os.path.splitext(video_file)
    subprocess.call(["ffmpeg", "-y", "-i", video_file, f"{filename}.{output_ext}"], 
                    stdout=subprocess.DEVNULL,
                    stderr=subprocess.STDOUT)
    return f"{filename}.{output_ext}"
#aca ejecutamos la funcion con el nombre del video que creamos guardamos 
#antes
input_video = 'video.mp4'
audio_file = video2mp3(input_video)


### Con esta funcion podes escuchar el audio en el notebook para comprobar que este bien (una boludez pero sirve de testeo)

In [24]:
from IPython.display import Audio
Audio(audio_file)

### Aca importamos e instanciamos el algoritmo pre-entrenado de Whisper en size "small", esto particularmente porque se va. a correr en local se lo hace en tamaño "small". Mientras mayor sea el tamaño elegido (el tamaño importa aca) mejor serán las transcripciones y las traducciones por la cantidad de parámetros que tenga el modelo, pero a la vez mayores serán los requerimientos para poder correrlo. En mi Mac me aguante sin reventarme la memoria y el CPU hasta el tamaño small (promedio diria yo). 

### Te dejo una tablita igual con los tamaños disponibles por si querés probar otro valor (cambiar donde dice "small" por "medium" "base" et...)


| Size   | Parameters | English-only model | Multilingual model |
|--------|------------|--------------------|-------------------|
| tiny   | 39 M       |        ✓           |         ✓         |
| base   | 74 M       |        ✓           |         ✓         |
| small  | 244 M      |        ✓           |         ✓         |
| medium | 769 M      |        ✓           |         ✓         |
| large  | 1550 M     |                     |         ✓         |


In [11]:
import whisper

model = whisper.load_model("small")

100%|████████████████████████████████████████| 461M/461M [00:03<00:00, 157MiB/s]


## Una vez instanciado el modelo en "model" se crea una función para retornar el resultado

In [12]:
def transcribe(audio):
    
    result = model.transcribe(audio_file, fp16=False)
    return result

## Ahora si ejecutamos la función

In [13]:
result = transcribe(audio_file)


In [14]:
# abrimos el file con el nombre de transcribe
file = open('transcribe.txt', 'w')

# escribimos el resultado dentro del file
file.write(result['text'])

# lo cerramos
file.close()

# Finalizado, el archivo transcribe.txt contiene el texto transcripto del video

In [15]:
!ls

sample_data  transcribe.txt  video.mp3	video.mp4
